# 1. Extracción y transformación de datos

Tras buscar información de diferentes fuentes elijo los datos que voy a extraer:

- CIMAVET, agencia española de medicamentos y productos sanitarios.
    - Base de datos completa con el Nomenclátor de prescripción: ➡ [url](https://cimavet.aemps.es/cimavet/publico/nomenclator.html)

De aquí descargo el archivo PrescripciónVET.xml, el cual meto en el .gitignore porque es muy pesado y no me deja guardar el proyecto. Luego obtendré la información convirtiendo el archivo en un diccionario.

- Purina:
    - Razas de gatos ➡ [url](https://www.purina.es/encuentra-mascota/razas-de-gato?page=%2C0)
    - Razas de perros ➡ [url](https://www.purina.es/encuentra-mascota/razas-de-perro)

De esta web realizaré el web scraping usando selenium.

- Censo de animales domésticos en madrid ➡ [url](https://datos.madrid.es/portal/site/egob/menuitem.c05c1f754a33a9fbe4b2e4b284f1a5a0/?vgnextoid=3e573d68ae8a6410VgnVCM1000000b205a0aRCRD&vgnextchannel=374512b9ace9f310VgnVCM100000171f5a0aRCRD&vgnextfmt=default)

Por último, obtendré esta información a partir del archivo censo_animales.csv.

In [1]:
# %pip install xmltodict
# %pip install selenium
# %pip install webdriver-manager

In [3]:
import re # utilizar expresiones regulares
import pandas as pd
import json
import xmltodict #para convertir archivos xml a diccionarios
import time

### Extraer y transformar datos de un archivo .xml

Lo primero que hago es descargar el archivo PrescripciónVET.xml. Lo abro y elimino los caracteres extraños que me dificultan la lectura con este .replace("&#x2;", ' '), luego convierto el archivo xml en un diccionario y empiezo a investigar sus keys. Voy a ir minando poco a poco... ([música para ambientarse mientras](https://www.youtube.com/watch?v=34CZjsEI1yU)) 

In [29]:
prescipcionVET = open("../data/data_raw/PrescipcionVET/PrescripcionVET.xml","r")
xml_prescipcionVET= prescipcionVET.read().replace("&#x2;", ' ')
prescipcionVET_dict =xmltodict.parse(xml_prescipcionVET)
prescipcionVET_dict.keys()

dict_keys(['aemps_prescripcion_vet'])

Realizando un punto de interrupción y depurando la celda, a la izquierda en ejecución y depuración, comienzo a meterme en las keys del diccionario, y observo que la información que me interesa se encuentra en los siguientes sitios: aemps_prescripcion_vet, prescription, dosisrecomendadaespecie y categoria.  Al final los datos con los que me quiero quedar son los medicamentos que tiene registrada actualmente la AEMPS para perros y gatos 

In [30]:
bloquePrescripcion = prescipcionVET_dict['aemps_prescripcion_vet']['prescription']
especies = ['Gatos', 'Perros']

def get_prescripcions_esp(bloquePrescripcion: list, especies: list): 
    """
    Para obtener una lista de diccionarios de medicamentos filtrado por especies.

    Args:
        bloquePrescripcion: el filtro de keys necesario para llegar a la info que quiero
        especies: las especies que quiera seleccionar

    Returns:
        Una lista de diccionarios filtrado por especie 
    """
    prescripciones = []
    for prescripcionDict in bloquePrescripcion:
        if not 'dosisrecomendadaespecie' in prescripcionDict:
            continue
        for dosisEspecieDict in prescripcionDict['dosisrecomendadaespecie']: # casi todos los valores eran dict, pero hay algunos str, en este caso los ignoramos y seguimos mirando lso demás
            if type(dosisEspecieDict) == str:
                continue
            if dosisEspecieDict['categoria'] in especies:
                prescripciones.append(prescripcionDict)
                break
    return prescripciones

prescripciones = get_prescripcions_esp(bloquePrescripcion, especies)  #con esta función obtengo una lista de diccionarios
prescripciones


[{'cod_nacion': '570004',
  'nro_definitivo': '1077 ESP',
  'nombre_med': 'AEROFAR',
  'fec_primera_aut': '1996-03-27',
  'fecha_alta_nomenclator': '2014-12-04',
  'cod_estado_registro_medicamento': '1',
  'cod_situacion_administrativa_medicamento': '1',
  'cod_estado_registro_formato': '1',
  'comercializado': 'SI',
  'posologia': 'https://cimavet.aemps.es/cimavet/pdfs/es/ft/1077%20ESP/1077_ESP_ft.pdf',
  'formato': 'AEROFAR, Envase pulverizador con 250 ml (180 g)',
  'contenido_total_envase': '180',
  'unidad_contenido_total_envase': '2',
  'prescripcion': 'SI',
  'administracion_exclusiva_veterinario': 'NO',
  'administracion_bajo_control_veterinario': 'SI',
  'homeopatico': 'NO',
  'contiene_edo': 'SI',
  'estupefaciente': 'NO',
  'psicotropo': 'NO',
  'base_a_plantas': 'NO',
  'ficha_tecnica': 'https://cimavet.aemps.es/cimavet/pdfs/es/ft/1077%20ESP/1077_ESP_ft.pdf',
  'prospecto': 'https://cimavet.aemps.es/cimavet/pdfs/es/p/1077%20ESP/1077_ESP_p.pdf',
  'titular': '3901',
  'sw_an

Consigo una lista de diccionarios con los medicamentos filtrados por especie, me falta transformar todavía los datos para poder crear un dataframe. Ahora compruebo que efectivamente me que quitado varias filas al escoger las especies

In [31]:
len(bloquePrescripcion) # estos son todos los medicamentos para animales

13866

In [32]:
len(prescripciones) #estos son los medicamentos específicos para gatos y perros que ya he filtrado

3115

In [33]:
especies = ['Gatos', 'Perros']

def dict_meds(prescripciones: list, especies: list): 
    """
    Para obtener un diccionario de medicamentos filtrado por especies. En las cuales tendremos los siguientes keys: Medicamento, Comercializado, Especie de destino

    Args:
        prescripciones: la lista de diccionarios con toda la información
        especies: la especie que quiero analizar

    Returns:
        Un diccionario filtrado por especie con estas keys: Medicamento, Comercializado, Especie de destino
    """
    Dict_meds_esp = {
        "Medicamento":[],
        "Comercializado":[],
        "Especie de destino":[]
        }
    for prescripcionDict in prescripciones:
        if not 'dosisrecomendadaespecie' in prescripcionDict:
            continue
        for dosisEspecieDict in prescripcionDict['dosisrecomendadaespecie']:
            if type(dosisEspecieDict) == str:
                continue
            if dosisEspecieDict['categoria'] in especies:
                Dict_meds_esp['Medicamento'].append(prescripcionDict['nombre_med'])
                Dict_meds_esp['Comercializado'].append(prescripcionDict['comercializado'])
                Dict_meds_esp['Especie de destino'].append(dosisEspecieDict['categoria'])
                break
    return Dict_meds_esp

resultado = dict_meds(prescripciones, especies)
resultado

{'Medicamento': ['AEROFAR',
  'CLAVUBAY 500 mg COMPRIMIDOS SABOR PARA PERROS',
  'CLAVUBAY 500 mg COMPRIMIDOS SABOR PARA PERROS',
  'CLAVUBAY 500 mg COMPRIMIDOS SABOR PARA PERROS',
  'CLAVUBAY 500 mg COMPRIMIDOS SABOR PARA PERROS',
  'ADOEQMINA 10 mg/ml SOLUCION CUTANEA # ADOEQMINA',
  'LOXICOM 5 mg/ml SOLUCION INYECTABLE PARA PERROS Y GATOS',
  'LOXICOM 5 mg/ml SOLUCION INYECTABLE PARA PERROS Y GATOS',
  'LOXICOM 5 mg/ml SOLUCION INYECTABLE PARA PERROS Y GATOS',
  'ALSIR 50 mg/ml SOLUCION INYECTABLE # ALSIR 5% SOLUCION INYECTABLE',
  'ALSIR 50 mg/ml SOLUCION INYECTABLE # ALSIR 5% SOLUCION INYECTABLE',
  'ALSIR 50 mg/ml SOLUCION INYECTABLE # ALSIR 5% SOLUCION INYECTABLE',
  'ALUSPRAY',
  'ANTISEDAN',
  'ATOPICA 100 mg CAPSULAS BLANDAS PARA PERROS',
  'ATOPICA 100 mg CAPSULAS BLANDAS PARA PERROS',
  'ATOPICA 100 mg CAPSULAS BLANDAS PARA PERROS',
  'ATOPICA 50 mg CAPSULAS BLANDAS PARA PERROS',
  'ATOPICA 50 mg CAPSULAS BLANDAS PARA PERROS',
  'ATOPICA 50 mg CAPSULAS BLANDAS PARA PERROS',

Con esta nueva función consigo crear una diccionario con 3 parámetros: Medicamento, Comercializado, Especie de destino. Finalmente lo acabo convirtiendo en un dataframe

In [34]:
data_meds = pd.DataFrame(resultado)
data_meds

Medicamento Comercializado  \
0                                               AEROFAR             SI   
1         CLAVUBAY 500 mg COMPRIMIDOS SABOR PARA PERROS             NO   
2         CLAVUBAY 500 mg COMPRIMIDOS SABOR PARA PERROS             NO   
3         CLAVUBAY 500 mg COMPRIMIDOS SABOR PARA PERROS             NO   
4         CLAVUBAY 500 mg COMPRIMIDOS SABOR PARA PERROS             NO   
...                                                 ...            ...   
3110  COXATAB 100 mg COMPRIMIDOS MASTICABLES PARA PE...             NO   
3111  KESIUM 200 mg / 50 mg COMPRIMIDOS MASTICABLES ...             NO   
3112  KESIUM 40 mg / 10 mg COMPRIMIDOS MASTICABLES P...             NO   
3113  KESIUM 50 mg / 12,5 mg COMPRIMIDOS MASTICABLES...             NO   
3114  BUPRELAB 0,3 mg/ml SOLUCION INYECTABLE PARA PE...             NO   

     Especie de destino  
0                Perros  
1                Perros  
2                Perros  
3                Perros  
4                Perros  
...                 ...  
3110             Perros  
3111             Perros  
3112              Gatos  
3113             Perros  
3114             Perros  

[3115 rows x 3 columns]

In [35]:
ruta_archivo = '../data/data_database/data_meds.csv'
data_meds.to_csv(ruta_archivo, index=False) 

### Extraer y transformar datos de una web

In [37]:
from selenium.webdriver.chrome.options import Options
from webdriver_manager.chrome import ChromeDriverManager
from selenium import webdriver

import warnings
warnings.filterwarnings('ignore')

from selenium.webdriver.common.by import By

Creo una función para crear el driver

In [38]:
def crearDriver():
    """
    Crear el driver de selenium

    Returns:
            Objeto Driver
    """
    opciones=Options()
    opciones.add_experimental_option('excludeSwitches', ['enable-automation'])
    opciones.add_experimental_option('useAutomationExtension', False)
    opciones.headless=False    # si True, no aperece la ventana (headless=no visible)
    opciones.add_argument('--start-maximized')         # comienza maximizado
    opciones.add_argument('--incognito')

    driver = webdriver.Chrome(options = opciones)
    return driver



Hago otra función para obtener las razas de gatos y perros

In [40]:
def extraerRazas(driver, url: str)->list:
    """
    Función para obtener una lista de las razas incluidas en la web de purina

    Args:
        driver: objeto driver 
        url: url especifica de la que queremos la info

    Returns:
        razas de animales (perros o gatos)
    """
    driver.get(url)
    time.sleep(3)

    cookiesButton = driver.find_element(By.XPATH, '//*[@id="onetrust-accept-btn-handler"]') #aceptar las coockies
    if cookiesButton:
        cookiesButton.click()
        time.sleep(2)

    razas = []

    while True:
        animales = driver.find_elements(By.CLASS_NAME, 'results-view-name') # por si llegamos a una pagina de la web donde no haya nombre de razas
        if not animales:
            break
        razas = razas + [e.text for e in animales] #extend

        next_page_button = [x for x in driver.find_element(By.CLASS_NAME, 'pager').find_elements(By.CSS_SELECTOR, 'a') if x.get_attribute('title')=='Go to next page'] # para pasar la pagina de la web

        if not next_page_button:   # Si no lo encuentra, no hay más páginas
            break
        try:
            next_page_button[0].click() # parecia que habia que hacer scroll, primero fallaba y a la segunda funcionaba
        except:
            next_page_button[0].click()
        finally:
            time.sleep(3)

    driver.quit()
    return razas


In [41]:
driver = crearDriver()
razasGato = extraerRazas(driver, url='https://www.purina.es/encuentra-mascota/razas-de-gato?page=%2C0')

Aquí ya he conseguido todas las razas, guardadas en forma de lista. Luego lo acabo convirtiendo en un dataframe. Y más adelante hago lo mismo con los perros

In [42]:
print(razasGato) 

['Abisinio', 'Americano de pelo duro', 'Asiático', 'Azul ruso', 'Balinés', 'Bengalí', 'Birmano', 'Bobtail japonés de pelo corto', 'Bobtail japonés de pelo largo', 'Bombay', 'Bosque de Noruega', 'Bosque de Siberia', 'Británico de pelo corto', 'Burmés', 'Burmilla', 'Chinchilla', 'Cornish rex', 'Cymric', 'Devon Rex', 'Exótico de pelo corto', 'Fold escocés', 'Khao Manee', 'Korat', 'Laperm', 'Maine coon', 'Manx', 'Mau egipcio', 'Mist australiano', 'Munchkin', 'Ocigato', 'Oriental de pelo corto', 'Oriental de pelo largo', 'Persa de pelo largo', 'Pixie bob', 'Ragdoll', 'Savannah', 'Selkirk rex', 'Siamés', 'Singapura', 'Snowshoe', 'Somalí', 'Sphynx', 'Tiffanie', 'Tonquinés', 'Van turco']


In [43]:
gatos = pd.DataFrame(razasGato, columns=['Razas de Gatos'])
gatos.head(10)

Razas de Gatos
0                       Abisinio
1         Americano de pelo duro
2                       Asiático
3                      Azul ruso
4                        Balinés
5                        Bengalí
6                        Birmano
7  Bobtail japonés de pelo corto
8  Bobtail japonés de pelo largo
9                         Bombay

In [44]:
ruta_archivo = '../data/data_database/razas_gatos.csv'
gatos.to_csv(ruta_archivo, index=False) 

In [46]:
driver = crearDriver()
razasPerro = extraerRazas(driver, url='https://www.purina.es/encuentra-mascota/razas-de-perro')

In [47]:
print(razasPerro)

['Affenpinscher', 'Afgano', 'Akita japonés', 'Basenji', 'Basset Azul de Gascuña', 'Basset Grifón vandeano (grande)', 'Basset Grifón vandeano (pequeño)', 'Basset Hound', 'Basset leonado de Bretaña', 'Beagle', 'Beauceron', 'Bedlington Terrier', 'Bergamasco', 'Bichón Boloñés', 'Bichón Frisé', 'Bloodhound', 'Bobtail (antiguo perro pastor inglés)', 'Border Collie', 'Border Terrier', 'Borzoi', 'Boston Terrier', 'Bóxer', 'Boyero de Berna', 'Boyero de Flandes', 'Bracco italiano', 'Braco alemán de pelo corto', 'Braco alemán de pelo duro', 'Braco de Weimar (de pelo corto y suave)', 'Braco húngaro', 'Braco húngaro de pelo duro', 'Bretón', 'Buhund noruego', 'Bull Terrier', 'Bull Terrier miniatura', 'Bulldog', 'Bulldog francés', 'Bullmastiff', 'Cairn Terrier', 'Caniche enano', 'Caniche grande', 'Caniche toy', 'Carlino', 'Cavalier King Charles Spaniel', 'Cazador de alces noruego (elkhound noruego)', 'Chihuahua (de pelo largo)', 'Chihuahua (de pelo suave)', 'Chin japonés', 'Chow chow (de pelo duro)',

In [48]:
perros = pd.DataFrame(razasPerro, columns=['Razas de Perros'])
perros

Razas de Perros
0                  Affenpinscher
1                         Afgano
2                  Akita japonés
3                        Basenji
4         Basset Azul de Gascuña
..                           ...
184               Vallhund sueco
185  West Highland White Terrier
186                      Whippet
187     Xoloitzcuintle (mediano)
188            Yorkshire Terrier

[189 rows x 1 columns]

In [49]:
ruta_archivo = '../data/data_database/razas_perros.csv'
perros.to_csv(ruta_archivo, index=False) 

### Extraer y transformar datos de un archivo .csv

In [50]:
data_censos = pd.read_csv('../data/data_raw/censo_animales.csv', sep=';', names=['AÑO', 'DISTRITO', 'ESPECIE CANINA', 'ESPECIE FELINA']) # leo el csv y le indico los nombres de las columnas

In [51]:
data_censos.head()

AÑO     DISTRITO  ESPECIE CANINA  ESPECIE FELINA
0   AÑO     DISTRITO  ESPECIE CANINA  ESPECIE FELINA
1  2021   ARGANZUELA           10843            5439
2  2021      BARAJAS            5139            1623
3  2021  CARABANCHEL           20595            6926
4  2021       CENTRO           16442            9878

Elimino la primera fila y reestablezco el índice

In [52]:
data_censos = data_censos.iloc[1:]
data_censos = data_censos.reset_index(drop=True)
data_censos


AÑO           DISTRITO ESPECIE CANINA ESPECIE FELINA
0    2021         ARGANZUELA          10843           5439
1    2021            BARAJAS           5139           1623
2    2021        CARABANCHEL          20595           6926
3    2021             CENTRO          16442           9878
4    2021          CHAMARTÍN          11361           4122
..    ...                ...            ...            ...
163  2014             TETUÁN          12301           2178
164  2014              USERA          11310            978
165  2014          VICÁLVARO           4584            505
166  2014  VILLA DE VALLECAS           7107            940
167  2014         VILLAVERDE          10467            851

[168 rows x 4 columns]

In [ ]:
ruta_archivo = '../data/data_database/censos.csv'
data_censos.to_csv(ruta_archivo, index=False) 

## Resumen

He obtenido y transformado la infomación de un archivo .xml sobre los medicamentos para animales en España convirtirndo el archivo en un diccionario e ir rebuscando hasta encontrar los datos que quería, en este caso el nombre del medicamento, si está comercializado o no y la especie de destino, que ya lo he filtrado a perros y gatos. Este diccionario lo convirtí a dataframe al final.

Tras esto, he sacado las razas de gatos y perros de la web de purina, utilizando selenium y obteniendo al final un dataframe.

Y finalmente he extraído los datos de un archivo .csv sobre los censos de perros y gatos de madrid, para convertir la info también en un dataframe.